In [63]:
# private dock midestuary
# Data points every 5 minuetes
# HDR is sea level (downriver), Hur is sea level (upriver)

import pandas as pd
import scipy.io as sio
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re


def Array_To_DataFrame(matDF, varName) :
    npArray = np.array([])
    for i in range (matDF[varName].shape[0]) :
        npArray = np.concatenate((npArray, matDF[varName][i].flatten()))
    return npArray
def matFile_To_DF(matFile) :
    tempDF = sio.loadmat(matFile)
    matDataMidFiltered = {}
    for dictKey in tempDF.keys() :
        if isinstance(tempDF[dictKey], np.ndarray) :
            if tempDF[dictKey].shape[0] > 1 :
                matDataMidFiltered.update({dictKey : tempDF[dictKey]})

    matMidDF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMidFiltered.items()})
    return matMidDF

def matFileCurrent_To_DF(matFile) :
    tempDF = sio.loadmat(matFile)
    matDataMidFiltered = {}
    for dictKey in tempDF.keys() :
        if isinstance(tempDF[dictKey], np.ndarray) :
            if tempDF[dictKey].shape[0] > 1 and tempDF[dictKey].shape[1] > 1 :
                for i in range(tempDF[dictKey].shape[0]) :
                    matDataMidFiltered.update({dictKey + '_z_' + str(i) : tempDF[dictKey][i]})
            elif dictKey == 'DN':
                matDataMidFiltered.update({dictKey : tempDF[dictKey]})

    matMidDF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMidFiltered.items()})
    matMidZ = pd.DataFrame({'z' : tempDF['Z'].flatten()})
    return (matMidDF, matMidZ, tempDF)

# import files for 2013-2014 and extract data
matDockDF = matFile_To_DF('2013_14\\P_processed_01.mat')
# import downriver current data
(matADCPDF, matADCPZDF, ADCPDict) = matFileCurrent_To_DF('2013_14\\adcp_2013_14.mat')
#mat lab date origin

ADCPDictUResized = np.resize(ADCPDict['U'], (ADCPDict['U'].shape[0], 38311))
for i in range(ADCPDict['U'].shape[0]) :
    #print(AquadoppDict['U'][i])
    #print(AquadoppDict['DN'])
    #print(np.interp(matDockDF['DN'], AquadoppDict['DN'].flatten(), AquadoppDict['U'][i]))
    tempNp = np.interp(matDockDF['DN'], ADCPDict['DN'].flatten(), ADCPDict['U'][i])
    ADCPDictUResized[i] = tempNp

origin = np.datetime64('0000-01-01', 'D') - np.timedelta64(1, 'D')

#convert DN to datetime
matDockDF['DN'] = (matDockDF['DN'] * np.timedelta64(24*3600000, 'ms') + origin + np.timedelta64(500, 'ms')).astype('datetime64[s]')
ADCPDict['DN'] = (ADCPDict['DN'] * np.timedelta64(24*3600000, 'ms') + origin + np.timedelta64(500, 'ms')).astype('datetime64[s]')

print(matADCPZDF)
seaLevelfig = px.line(x = matDockDF['DN'], y = [matDockDF['Hdr'], matDockDF['Hur']], color_discrete_sequence= ["black", "blue"], title = "Sea Level")
seaLevelFigLabel = ['Downriver Sea Level', 'Upriver Sea Level']
for idx in range(len(seaLevelFigLabel)):
    seaLevelfig.data[idx].name = seaLevelFigLabel[idx]
    seaLevelfig.data[idx].hovertemplate = 'variable=' + seaLevelFigLabel[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    seaLevelfig.data[idx].legendgroup = seaLevelFigLabel[idx]


seaLevelfig.update_layout(title=dict(text= "Sea Level for 2013-2014", font=dict(size=25)))
seaLevelfig.update_xaxes(tickangle=30)
seaLevelfig.update_xaxes(rangeslider_visible=True)
seaLevelfig.update_xaxes(range = [pd.Timestamp('2013-10-28'),pd.Timestamp('2014-03-17')])
seaLevelfig.update_layout(xaxis_title="Date", yaxis_title="Sea Level (m)", legend_title="Locations")
#seaLevelfig.show()

# testing heat maps / plotting under the curve

# Align and interpolate U to match dock time series

#figHm = px.imshow(AquadoppDict['U'], aspect='auto', origin='lower', labels=dict(x="Time Index", y="Depth Index", color="Along Channel Velocity (m/s)"), title="Downriver Velocity Profile 2013-2014")
figHm = go.Figure(data = go.Heatmap(z=ADCPDictUResized, x=matDockDF['DN'], y=matADCPZDF['z'], colorscale='cividis', colorbar=dict(title="Along Channel Velocity (m/s)")))
#px.imshow(AquadoppDict['v'], aspect='auto', origin='lower', labels=dict(x="Time Index", y="Depth Index", color="Velocity (m/s)"), title="Cross-river Velocity Profile 2013-2014")
# Create and add the second trace (line plot)
figHm.add_trace(go.Scatter(x = matDockDF['DN'], y = matDockDF['Hdr'], mode = 'lines', name = 'Downriver Sea Level', line=dict(color='black')))
figHm.update_layout(title_text="Sea Level at Downriver Location and Current Profile 2013-2014")
figHm.update_layout(xaxis_title = "Date", yaxis_title = "Depth (m)")
figHm.show()


       z
0   1.03
1   1.28
2   1.53
3   1.78
4   2.03
5   2.28
6   2.53
7   2.78
8   3.03
9   3.28
10  3.53
11  3.78
12  4.03
13  4.28
14  4.53
15  4.78
16  5.03
